In [77]:
!pip install datasets 
!pip install gensim
!pip install sklearn
!pip install pandas
!pip install fasttext
!pip install umap-learn
!pip install umap-learn[plot]
!pip install matplotlib

In [2]:
#Downloads the berkley dataset to be cleaned.
import datasets
dataset = datasets.load_dataset('ucberkeley-dlab/measuring-hate-speech', 'binary') 
df = dataset['train'].to_pandas()

#Convert the hate_speech_score into a true or a false
for i in range(len(df)):
    if df.loc[i,"hate_speech_score"] <= 0:
        df.loc[i,"classification"] = '__label__Acceptable'
    else:
        df.loc[i,"classification"] = '__label__Unacceptable'

Using custom data configuration ucberkeley-dlab--measuring-hate-speech-f91f636a830ad73c


Extracting data files:   0%|          | 0/1 [00:00<?, ?it/s]

Dataset parquet downloaded and prepared to /root/.cache/huggingface/datasets/parquet/ucberkeley-dlab--measuring-hate-speech-f91f636a830ad73c/0.0.0/0b6d5799bb726b24ad7fc7be720c170d8e497f575d02d47537de9a5bac074901. Subsequent calls will reuse this data.


  0%|          | 0/1 [00:00<?, ?it/s]

In [3]:
from gensim.utils import simple_preprocess
from gensim.parsing.porter import PorterStemmer
from sklearn.model_selection import train_test_split
import pandas as pd

In [4]:
df['stemmed_tokens']=df['text']
X_train,X_test,Y_train,Y_test=train_test_split(df['stemmed_tokens'],df['classification'])
X_train = X_train.reset_index()
X_test = X_test.reset_index()
Y_train = Y_train.to_frame()
Y_train = Y_train.reset_index()
Y_test = Y_test.to_frame()
Y_test = Y_test.reset_index()

In [5]:
#Save the files as txt files, required for fasttext
train=pd.concat([Y_train['classification'],X_train['stemmed_tokens']],axis=1)
test=pd.concat([Y_test['classification'],X_test['stemmed_tokens']],axis=1)
train.to_csv('data.train.txt', sep=' ', index=False,encoding="utf-8")
test.to_csv('data.test.txt', sep=' ', index=False,encoding="utf-8")

In [6]:
# fasttext processing
import fasttext
model = fasttext.train_supervised('data.train.txt')

# Visualisation below


In [7]:
print(train)
print(model.get_dimension())

               classification  \
0         __label__Acceptable   
1       __label__Unacceptable   
2       __label__Unacceptable   
3         __label__Acceptable   
4         __label__Acceptable   
...                       ...   
101662  __label__Unacceptable   
101663    __label__Acceptable   
101664    __label__Acceptable   
101665    __label__Acceptable   
101666    __label__Acceptable   

                                           stemmed_tokens  
0       when Muslim women wear hijab: 😒 when non-Musli...  
1       GET RID OF THOSE FUCKING MUSLIMS! the nasty on...  
2       What a fucking douchebag. Fuck religion and fu...  
3       A nigga with no job can't never watch they kid...  
4       Keep laughing everyone, our tax dollars paid f...  
...                                                   ...  
101662  I'm proud of this! Nothing more than a little ...  
101663        Because on Reddit only women can be stupid.  
101664  @Moh_Alhouthi Mohammed Ali Al-Houthi: The UAE'...  
101

In [67]:
#Play around with the model here
print(model.words)
print(model.labels)
word_list=[]
vector_list=[]
label_list=[]
for word in model.words:
  vector=model.get_word_vector(word)
  label=model.predict(word)[0][0].replace('__label__','')
  #Labels have to be numerical for Umap
  if label=='Acceptable':
    label=0
  else:
    label=1
  word_list.append(word)
  vector_list.append(vector)
  label_list.append(label)
visualisation_df=pd.DataFrame(list(zip(vector_list,word_list, label_list)),columns =['vector','word', 'label'])


['</s>', 'the', 'to', 'and', 'a', 'of', 'you', 'is', 'in', 'are', 'that', 'I', 'be', 'for', 'on', 'your', 'have', 'all', 'with', 'people', 'they', 'URL"', 'not', 'this', 'their', 'it', 'like', 'we', 'but', 'just', 'my', 'so', 'fucking', 'them', 'as', 'will', 'out', 'should', 'women', 'our', 'or', 'because', 'up', 'from', 'if', "don't", 'at', 'fuck', 'get', 'who', 'hate', 'these', 'being', 'her', 'go', 'white', 'by', 'no', 'do', 'what', 'was', 'You', 'more', 'me', 'when', '"I', 'back', 'about', 'need', 'even', 'can', 'one', 'how', 'she', 'would', 'They', 'human', "I'm", 'only', 'want', 'And', 'an', '&', "it's", 'know', 'We', 'men', 'there', 'kill', 'black', 'than', 'were', 'stupid', 'i', 'think', 'why', 'he', 'some', 'make', 'The', 'ass', 'look', 'any', 'been', 'every', 'am', 'own', 'has', 'If', 'see', 'his', 'other', 'many', "you're", 'bitch', 'right', 'here', 'country', 'love', 'gay', 'same', 'really', 'niggers', 'shit', 'over', 'pussy', 'now', 'then', "It's", 'very', 'off', 'America'

In [60]:
print(visualisation_df['label'].to_numpy()[:10])

['Acceptable' 'Acceptable' 'Acceptable' 'Acceptable' 'Acceptable'
 'Acceptable' 'Acceptable' 'Acceptable' 'Acceptable' 'Acceptable']


In [104]:
import umap
size=50000
data=visualisation_df['vector'].tolist()
labels=visualisation_df['label'].tolist()
words=visualisation_df['word'].tolist()
supervised_embedding = umap.UMAP().fit(data[:size],y=labels[:size])
unsupervised_embedding = umap.UMAP().fit(data[:size])

In [105]:
import numpy as np
hover_data = pd.DataFrame({'index':np.arange(size),
                           'item':words[:size],
                           'label':labels[:size]})
hover_data['label'] = hover_data.label.map(
    {
        0:'Acceptable',
        1:'Unacceptable'
    })
umap.plot.output_notebook()
p = umap.plot.interactive(supervised_embedding, labels=labels[:size], hover_data=hover_data[:size], point_size=5)
umap.plot.show(p)

In [106]:
import numpy as np
hover_data = pd.DataFrame({'index':np.arange(size),
                           'item':words[:size],
                           'label':labels[:size]})
hover_data['label'] = hover_data.label.map(
    {
        0:'Acceptable',
        1:'Unacceptable'
    })
umap.plot.output_notebook()
p = umap.plot.interactive(unsupervised_embedding, labels=labels[:size], hover_data=hover_data[:size], point_size=5)
umap.plot.show(p)